Problem Set 8: Network Flow and Bipartite Matching
========================



In [ ]:
# You may need to `pip install networkx` and `pip install numpy`
# We'll use NetworkX as in previous problem sets.
import networkx as nx
# https://networkx.github.io/documentation/stable/tutorial.html

import numpy as np

#Visualization tools
import pylab
import matplotlib
%matplotlib inline
import matplotlib.patches as patches
matplotlib.rcParams['figure.figsize'] = (5,5)

In [ ]:
# Simple graph to test
# edge['c'] is the capacity
G = nx.DiGraph()
G.add_edge('s', 'a', c=2)
G.add_edge('s', 'b', c=1)
G.add_edge('a', 'b', c=2)
G.add_edge('a', 't', c=1)
G.add_edge('b', 't', c=2)

def draw_func(G, label_func, pos_func=nx.planar_layout):
    nx.draw_networkx(G, pos=pos_func(G), with_labels=True, node_size=600)
    nx.draw_networkx_edge_labels(G, pos=pos_func(G),
                             edge_labels={e: label_func(G, e) for e in G.edges})
    
    
draw_func(G, lambda G, e: G.edges[e]['c'])

Network Flow Code
--------------------

In [ ]:
def find_path(residual, s, t):
    """Find the shortest s->t path over nonzero edges in residual graph."""
    # Remove zero-weight edges, and use a copy so we don't change the graph
    r = residual.copy()
    r.remove_edges_from([e for e in r.edges if
                         r.edges[e]['c'] == 0])
    # and find the shortest path      
    try:
        return nx.shortest_path(r, s, t)
    except nx.exception.NetworkXNoPath:
        return None

def max_flow(G, s, t):
    """Find the maximum s-t flow in a graph via Ford-Fulkerson.
    
    G.edges[(u,v)]['c'] denotes the capacity of the u->v edge.
    
    Return a dictionary of the flows where
      flow[(u,v)] = flow from u->v in a max flow solution.
    """
    residual = G.copy()
    while True:
        augmenting_path = find_path(residual, s, t)
        if augmenting_path is None:
            break
            
        # Find the capacity along the path
        path_edges = list(zip(augmenting_path[:-1], augmenting_path[1:]))
        path_capacities = [residual.edges[e]['c'] for e in path_edges]
        flow_this_round = min(path_capacities)
        #Subtract from forward edges, add to reverse
        for u,v in path_edges:
            residual.edges[(u,v)]['c'] -= flow_this_round
            if (v,u) not in residual.edges:
                residual.add_edge(v,u, c=0)
            residual.edges[(v,u)]['c'] += flow_this_round

    # Part (a): Oops! We forgot to actually compute the `flow`
    # dictionary.  Rectify this.
    flow = {}
    ...
    return flow

In [ ]:
# Let's try pushing flow
flow = max_flow(G, 's', 't')
total_flow = sum(flow.get(('s', u), 0) - flow.get((u, 's'), 0) for u in G)
print(f"Got {total_flow} flow.")

print(f"Full dictionary: {flow}")

draw_func(G, lambda G, e: f"cap = {G.edges[e]['c']}\n flow={flow[e]}")

#Check that this works; for each edge, the flow should be between 0 and the capacity.    


Tiling Problem
===

We now solve the following problem.  You are given a subset of squares in a grid.  You want to place as many dominoes (= 2x1 tiles) on this subset as possible, without overlaps.

In [ ]:
# Create and display an instance of the problem

def random_mask(r, c, p):
    return np.random.random(size=(r,c)) > p

def draw_rectangle(lx, ly, widthx, widthy, **kws):
    pylab.gca().add_patch(patches.Rectangle((lx, ly), widthx, widthy,
                                           **kws))

def display_tiling_problem(mask):
    r, c = mask.shape
    for i in range(r):
        for j in range(c):
            if mask[i][j]:
                draw_rectangle(i, j, 1, 1, lw=1, ec='black')
    pylab.xlim(0, r)
    pylab.ylim(0, c)

np.random.seed(1)
m = random_mask(10, 10, 0.3)
pylab.figure(figsize=(5,5))
display_tiling_problem(m)
    

In [ ]:
# Let's start with an (incorrect) greedy solution.
# (On some inputs the greedy gets lucky and works, though.)

def greedy_tiling(mask):
    # Return a list of pairs of vertices, corresponding to the dominos placed down.
    # The plan is, for each square with mask[i][j] = 1, to try to place a domino there
    # and if we can, set mask = 0 on those positions.
    mask = mask.copy()
    tiles = set()
    adjacencies = [(0, 1), (0, -1), (-1, 0), (1, 0)]
    r, c = mask.shape
    for u in np.ndindex(mask.shape):
        if mask[u]:
            for dx, dy in adjacencies:
                v = (u[0]+dx, u[1]+dy)
                if 0 <= v[0] < r and 0 <= v[1] < c:
                    if mask[v]:
                        tiles.add((u, v))
                        mask[u] = mask[v] = 0
                        break
    return tiles

greedy_result = greedy_tiling(m)
print("Greedy tiling:", len(greedy_result))


In [ ]:
#And let's show this solution

def display_tiling_solution(mask, pairs):
    display_tiling_problem(mask)
    for (u,v) in pairs:
        if u == 's' or v == 't':
            continue
        pylab.plot([u[0] + .5, v[0]+ .5], [u[1]+ .5, v[1]+ .5], 'k',
                  lw=10)
    
display_tiling_solution(m, greedy_result)
# This should display the associated tiling
# You shouldn't be able to place another domino without rearranging them.

Correct Algorithm
---

This problem is a *bipartite matching* problem, which is solved using max flow/min cut.  The idea is that you color each square black or white in alternating colors, like in a chessboard.  Then each domino lies on one black square and one white square.  

We draw a graph as follows:

   (source vertex t) -> all white tiles -> all black tiles -> (sink vertex t)
   
The source connects to each white tile with a weight-1 edge; each white tile connects to each adjacent black tile with a weight-1 edge; and finally each black tile connects to the sink with a weight-1 edge.

The max s-t flow on this graph equals the maximum number of dominos that can be placed, and the (white-black) edges used in the flow correspond to the dominos placed.

This is because:

 - If you can place k dominos, you can have k flow by pushing 1 flow through each domino (from source to white square of domino, to black square, to sink), so max flow >= k.
 
 - If you have a max flow F, you can assume it is integral.  Then each (white->black) edge in the flow has 1 flow along it that must come in on the white square [because that's the only way in] and leave on the black [because that's the only way out]. Since the (source->white) and (black -> sink) edges only have 1 capacity, no two (white->black) edges can share a square.  So this gives a size-k tiling of dominos that don't overlap.

Therefore we can solve the tiling problem by constructing the graph and performing max flow.

In [ ]:
def matching_graph_for_tiling_mask(mask):
    r, c = mask.shape
    G = nx.DiGraph()
    G.add_nodes_from((a,b) for a in range(r) for b in range(c)
                     if mask[a][b])
    G.add_nodes_from(['s', 't'])
    adjacencies = [(0, 1), (0, -1), (-1, 0), (1, 0)]
    for u in G.nodes:
        if u in ['s', 't']:
            continue
        i, j = u
        if (i + j) % 2 == 0:
            G.add_edge(u, 't', c=1)
        else:
            G.add_edge('s', u, c=1)
            for dx, dy in adjacencies:
                v = (i + dx, j + dy)
                if v in G.nodes:
                    G.add_edge(u, v, c=1)
    return G

G = matching_graph_for_tiling_mask(m)
            

In [ ]:
f = max_flow(G, 's', 't')
total_flow = ...           # (b) XXX compute me
print("Found solution with total flow", total_flow)
# This should work, and find positive flow

display_tiling_solution(m, [k for k in f.keys() if f[k] > 0])

In [ ]:
# Let's run the greedy and net flow solutions side by side.
# Rerun this until the two perform differently.

m = random_mask(15, 15, 0.25)
G = matching_graph_for_tiling_mask(m)
f = max_flow(G, 's', 't')
total_flow = ...
greedy_result = greedy_tiling(m)
print(f"Net flow: {total_flow} vs greedy: {len(greedy_result)}")
pylab.figure(figsize=(10,5))
pylab.subplot(121)
display_tiling_solution(m, [k for k in f.keys() if f[k] > 0])
pylab.subplot(122)
display_tiling_solution(m, greedy_result)
